# Práctica 1B: Análisis Exploratorio del Dataset Wine Quality
## Autor: Valentín Rodríguez
### UT1: EDA & Fuentes | Práctica Alternativa

## Objetivo
Realizar un análisis exploratorio completo del dataset Wine Quality para identificar patrones, relaciones y características que influyen en la calidad del vino.

## Dataset
El dataset Wine Quality contiene 1,599 muestras de vino tinto con 11 atributos fisicoquímicos y una variable objetivo de calidad (0-10).


In [ ]:
# Importar librerías necesarias
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')

# Configurar estilo de visualizaciones
plt.style.use('seaborn-v0_8')
sns.set_palette("husl")
plt.rcParams['figure.figsize'] = (12, 8)

print("Librerías importadas correctamente")


In [ ]:
# Cargar el dataset Wine Quality
url = 'https://archive.ics.uci.edu/ml/machine-learning-databases/wine-quality/winequality-red.csv'
wine_df = pd.read_csv(url, sep=';')

print("Dataset Wine Quality cargado exitosamente")
print(f"Dimensiones: {wine_df.shape}")
wine_df.head()


In [ ]:
# Información general del dataset
print("=== INFORMACIÓN GENERAL DEL DATASET ===")
print(f"Forma del dataset: {wine_df.shape}")
print(f"\nTipos de datos:")
print(wine_df.dtypes)
print(f"\nValores faltantes:")
print(wine_df.isnull().sum())
print(f"\nEstadísticas descriptivas:")
wine_df.describe()


In [ ]:
# Análisis de la variable objetivo
print("=== ANÁLISIS DE LA VARIABLE OBJETIVO (QUALITY) ===")
print(f"Distribución de calidad del vino:")
print(wine_df['quality'].value_counts().sort_index())

# Visualización de la distribución de calidad
plt.figure(figsize=(10, 6))
plt.subplot(1, 2, 1)
wine_df['quality'].value_counts().sort_index().plot(kind='bar', color='darkred')
plt.title('Distribución de Calidad del Vino')
plt.xlabel('Calidad')
plt.ylabel('Frecuencia')
plt.xticks(rotation=0)

plt.subplot(1, 2, 2)
wine_df['quality'].hist(bins=6, color='darkred', alpha=0.7)
plt.title('Histograma de Calidad')
plt.xlabel('Calidad')
plt.ylabel('Frecuencia')

plt.tight_layout()
plt.savefig('wine-quality-distributions.png', dpi=300, bbox_inches='tight')
plt.show()


In [ ]:
# Análisis de distribuciones de variables fisicoquímicas
print("=== ANÁLISIS DE DISTRIBUCIONES ===")

# Seleccionar variables principales para análisis
main_features = ['fixed acidity', 'volatile acidity', 'citric acid', 'residual sugar', 
                'chlorides', 'free sulfur dioxide', 'total sulfur dioxide', 'density', 
                'pH', 'sulphates', 'alcohol']

# Crear subplots para distribuciones
fig, axes = plt.subplots(3, 4, figsize=(16, 12))
axes = axes.ravel()

for i, feature in enumerate(main_features):
    if i < len(axes):
        wine_df[feature].hist(ax=axes[i], bins=20, alpha=0.7, color='darkred')
        axes[i].set_title(f'Distribución de {feature}')
        axes[i].set_xlabel(feature)
        axes[i].set_ylabel('Frecuencia')

# Eliminar subplots vacíos
for i in range(len(main_features), len(axes)):
    fig.delaxes(axes[i])

plt.tight_layout()
plt.show()


In [ ]:
# Análisis de correlaciones
print("=== MATRIZ DE CORRELACIONES ===")

# Calcular matriz de correlaciones
correlation_matrix = wine_df.corr()

# Visualizar heatmap de correlaciones
plt.figure(figsize=(12, 10))
mask = np.triu(np.ones_like(correlation_matrix, dtype=bool))
sns.heatmap(correlation_matrix, mask=mask, annot=True, cmap='RdBu_r', center=0,
            square=True, linewidths=0.5, cbar_kws={"shrink": 0.8})
plt.title('Matriz de Correlaciones - Wine Quality Dataset')
plt.tight_layout()
plt.savefig('wine-quality-correlations.png', dpi=300, bbox_inches='tight')
plt.show()

# Mostrar correlaciones más altas con quality
quality_corr = correlation_matrix['quality'].abs().sort_values(ascending=False)
print("\nCorrelaciones con Quality (ordenadas por magnitud):")
print(quality_corr[1:])  # Excluir quality consigo misma


In [ ]:
# Boxplots por calidad
print("=== ANÁLISIS POR NIVELES DE CALIDAD ===")

# Crear categorías de calidad
def categorize_quality(quality):
    if quality <= 4:
        return 'Baja (≤4)'
    elif quality <= 6:
        return 'Media (5-6)'
    else:
        return 'Alta (≥7)'

wine_df['quality_category'] = wine_df['quality'].apply(categorize_quality)

# Boxplots para variables más correlacionadas con quality
top_features = ['alcohol', 'volatile acidity', 'sulphates', 'citric acid', 'total sulfur dioxide']

fig, axes = plt.subplots(2, 3, figsize=(15, 10))
axes = axes.ravel()

for i, feature in enumerate(top_features):
    if i < len(axes):
        sns.boxplot(data=wine_df, x='quality_category', y=feature, ax=axes[i])
        axes[i].set_title(f'{feature} por Categoría de Calidad')
        axes[i].tick_params(axis='x', rotation=45)

# Eliminar subplot vacío
fig.delaxes(axes[5])

plt.tight_layout()
plt.savefig('wine-quality-quality-vs-features.png', dpi=300, bbox_inches='tight')
plt.show()


In [ ]:
# Pairplot para variables más importantes
print("=== ANÁLISIS MULTIVARIADO ===")

# Seleccionar variables más relevantes
important_features = ['alcohol', 'volatile acidity', 'sulphates', 'quality']

# Crear pairplot
pairplot = sns.pairplot(wine_df[important_features], hue='quality', palette='Reds')
pairplot.fig.suptitle('Pairplot de Variables Importantes del Wine Quality Dataset', y=1.02)
pairplot.savefig('wine-quality-pairplot.png', dpi=300, bbox_inches='tight')
plt.show()


In [ ]:
# Análisis de outliers
print("=== ANÁLISIS DE OUTLIERS ===")

# Función para detectar outliers usando IQR
def detect_outliers(df, column):
    Q1 = df[column].quantile(0.25)
    Q3 = df[column].quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    return df[(df[column] < lower_bound) | (df[column] > upper_bound)]

# Detectar outliers en variables principales
outlier_summary = {}
for feature in main_features:
    outliers = detect_outliers(wine_df, feature)
    outlier_summary[feature] = len(outliers)

# Crear visualización de outliers
plt.figure(figsize=(12, 6))
features_with_outliers = [k for k, v in outlier_summary.items() if v > 0]
outlier_counts = [v for k, v in outlier_summary.items() if v > 0]

plt.bar(features_with_outliers, outlier_counts, color='darkred', alpha=0.7)
plt.title('Número de Outliers por Variable')
plt.xlabel('Variables')
plt.ylabel('Número de Outliers')
plt.xticks(rotation=45)
plt.tight_layout()
plt.show()

print(f"\nVariables con outliers: {len(features_with_outliers)}")
for feature, count in zip(features_with_outliers, outlier_counts):
    print(f"{feature}: {count} outliers")


In [ ]:
# Resumen de insights principales
print("=== RESUMEN DE INSIGHTS PRINCIPALES ===")
print("\n1. CARACTERÍSTICAS DEL DATASET:")
print(f"   - Total de muestras: {wine_df.shape[0]}")
print(f"   - Variables fisicoquímicas: {wine_df.shape[1]-1}")
print(f"   - Rango de calidad: {wine_df['quality'].min()} - {wine_df['quality'].max()}")

print("\n2. DISTRIBUCIÓN DE CALIDAD:")
quality_dist = wine_df['quality'].value_counts().sort_index()
print(f"   - Calidad más común: {quality_dist.idxmax()} ({quality_dist.max()} muestras)")
print(f"   - Calidad menos común: {quality_dist.idxmin()} ({quality_dist.min()} muestras)")

print("\n3. VARIABLES MÁS INFLUYENTES EN LA CALIDAD:")
top_correlations = correlation_matrix['quality'].abs().sort_values(ascending=False)[1:4]
for feature, corr in top_correlations.items():
    print(f"   - {feature}: {corr:.3f}")

print("\n4. PATRONES IDENTIFICADOS:")
print("   - El alcohol tiene la correlación más alta con la calidad")
print("   - La acidez volátil muestra correlación negativa fuerte")
print("   - Los sulfatos también influyen positivamente en la calidad")
print("   - Existe variabilidad significativa en las características fisicoquímicas")


## Conclusiones

El análisis exploratorio del dataset Wine Quality revela patrones interesantes en las características fisicoquímicas que influyen en la calidad del vino. Las variables más importantes identificadas son el contenido de alcohol, la acidez volátil y los sulfatos, que muestran correlaciones significativas con la calidad del vino.

Este análisis sienta las bases para futuros modelos de clasificación y predicción de calidad del vino basados en sus propiedades fisicoquímicas.
